In [1]:
import wandb
import sys
import matplotlib.pyplot as plt
import scprep
import pandas as pd
sys.path.append('../../src/')
from train import load_data
# from diffusion import DiffusionModel
# from evaluate import get_results
from omegaconf import OmegaConf
# from main import load_data, make_model
import numpy as np
import os
import glob
import matplotlib.animation as animation
from matplotlib.animation import PillowWriter
import torch
from model2 import Autoencoder, Preprocessor
import magic
import torch
import pathlib
wandb.login()
api = wandb.Api()

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: xingzhis. Use `wandb login --relogin` to force relogin


In [2]:
from procrustes import Procrustes

In [3]:
from plotly3d.plot import scatter

In [89]:
entity = "xingzhis"
project = "dmae"
sweep_id = 'f3ug933e'
sweep = api.sweep(f"{entity}/{project}/{sweep_id}")
# Initialize an empty list to store run data
runs_data = []

# Iterate through each run in the sweep
for run in sweep.runs:
    # Extract metrics and configs
    metrics = run.summary._json_dict
    configs = run.config
    
    # Combine metrics and configs, and add run ID
    combined_data = {**metrics, **configs, "run_id": run.id}
    
    # Append the combined data to the list
    runs_data.append(combined_data)

# Create a DataFrame from the runs data
df = pd.DataFrame(runs_data)

In [94]:
len(np.unique([run.id for run in sweep.runs]))

68

In [90]:
len(df['run_id'].unique())

68

In [71]:
df['data.name'].unique()

array(['hemisphere', 'hemisphere_hi_dim2', 'eb_subset_all'], dtype=object)

In [72]:
df.columns

Index(['validation/reconstr_loss', 'epoch', '_wandb', 'train/loss_epoch',
       'train/dist_loss_epoch', 'trainer/global_step', 'train/dist_loss_step',
       'validation/dist_loss', 'validation/loss', 'train/cycle_loss_step',
       'train/reconstr_loss_step', '_step', '_timestamp', 'train/loss_step',
       'train/reconstr_loss_epoch', '_runtime', 'validation/cycle_loss',
       'train/cycle_loss_epoch', 'data', 'loss', 'path', 'logger', 'decoder',
       'encoder', 'training', 'data.name', 'data.root', 'dimensions',
       'preprocessor', 'cfg/data/name', 'cfg/data/root', 'cfg/path/root',
       'training.mode', 'cfg/path/model', 'cfg/logger/tags', 'cfg/training/lr',
       'decoder.dropout', 'encoder.dropout', 'cfg/data/filetype',
       'cfg/logger/entity', 'cfg/training/mode', 'cfg/training/seed',
       'dimensions.latent', 'loss.weights.dist', 'cfg/logger/project',
       'decoder.batch_norm', 'encoder.batch_norm', 'loss.weights.cycle',
       'cfg/decoder/dropout', 'cfg/dimen

In [73]:
df['data.name'].value_counts()

data.name
hemisphere            24
hemisphere_hi_dim2    24
eb_subset_all         24
Name: count, dtype: int64

In [74]:
df['loss.weights.cycle']

0     10.0
1      1.0
2     10.0
3      0.3
4      1.0
      ... 
67     0.3
68     1.0
69    10.0
70     0.3
71     1.0
Name: loss.weights.cycle, Length: 72, dtype: float64

In [75]:
df[(df['data.name'] == 'hemisphere_hi_dim2') & (df['training.mode'] == 'end2end')].sort_values(['validation/dist_loss', 'validation/reconstr_loss'])[['validation/loss', 'validation/dist_loss', 'validation/reconstr_loss', 'run_id', 'cfg/encoder/dropout', 'cfg/loss/dist_mse_decay', 'cfg/loss/weights/cycle', 'cfg/dimensions/latent', 'cfg/data/root']]

validation/loss  validation/dist_loss  validation/reconstr_loss    run_id  \
40        16.057903              0.055091                 36.422749  v293f2sq   
42        16.510689              0.070366                 34.517422  qaxtnto7   
43        18.977627              0.071655                 35.806419  4l1f9tf0   
44        20.382963              0.077283                 44.912094  4c1l1342   
27        20.271406              0.083375                 42.769596  b7nbdv5s   
31        20.271406              0.083375                 42.769596  b7nbdv5s   
26        22.641367              0.093116                 43.711887  x4entswc   
34        18.731152              0.095705                 35.298462  gosax54q   
32        25.863255              0.098201                 56.772491  h6po258q   
37        19.481398              0.099623                 36.397011  wkcueopl   
36        24.233803              0.124670                 45.296825  oqh8wwxr   
45        23.258244              0.127067                 34.798817  2tod3mjl   
23        30.341431              0.129671                 57.623428  9u8lg6lx   
35        27.159704              0.134674                 48.499401  vxnv620j   
24        27.522871              0.173235                 43.742989  p5csht1r   
30        27.522871              0.173235                 43.742989  p5csht1r   
28        28.754755              0.181636                 44.734386  7kk84eks   
29        31.466578              0.183301                 44.823872  12w0fjz5   
53        34.175140              0.241473                 48.051060  rbrt5t0p   
41        35.051350              0.254571                 46.949203  qaerrh7q   
38        38.294197              0.259363                 46.253384  q3672kr4   
46        43.613380              0.320913                 58.139244  smmularu   
33        46.345699              0.366025                 56.203323  08mktylv   
39        49.671169              0.373440                 60.235413  9aiyxkcq   

    cfg/encoder/dropout  cfg/loss/dist_mse_decay  cfg/loss/weights/cycle  \
40                    0                      0.5                     1.0   
42                    0                      0.5                     0.3   
43                    0                      0.5                    10.0   
44                    0                      0.5                     0.3   
27                    0                      0.5                     1.0   
31                    0                      0.5                     1.0   
26                    0                      0.5                    10.0   
34                    0                      0.5                     0.3   
32                    0                      0.5                     1.0   
37                    0                      0.5                     1.0   
36                    0                      0.5                     1.0   
45                    0                      0.5                    10.0   
23                    0                      0.5                    10.0   
35                    0                      0.5                    10.0   
24                    0                      0.5                     0.3   
30                    0                      0.5                     0.3   
28                    0                      0.5                     1.0   
29                    0                      0.5                    10.0   
53                    0                      0.5                     0.3   
41                    0                      0.5                     1.0   
38                    0                      0.5                    10.0   
46                    0                      0.5                     1.0   
33                    0                      0.5                     0.3   
39                    0                      0.5                    10.0   

    cfg/dimensions/latent                                      cfg/data/root 

In [76]:
len(df)

72

In [77]:
for v in df[(df['data.name'] == 'hemisphere_hi_dim2') & (df['training.mode'] == 'end2end')].sort_values(['validation/dist_loss', 'validation/reconstr_loss'])[['validation/loss', 'validation/dist_loss', 'validation/reconstr_loss', 'run_id', 'cfg/encoder/dropout', 'cfg/loss/dist_mse_decay', 'cfg/loss/weights/cycle', 'cfg/dimensions/latent', 'cfg/data/root']]['cfg/data/root'].values:
    print(v)

../data/negative_sampling_new/dist_mask_True/hi-freq/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq/1.0/
../data/negative_sampling_new/dist_mask_True/hi-freq-no-add/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq-no-add/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq-no-add/1.5/
../data/negative_sampling_new/dist_mask_False/hi-freq/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq-no-add/1.0/
../data/negative_sampling_new/dist_mask_False/hi-freq/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq/1.0/
../data/negative_sampling_new/dist_mask_False/hi-freq/1.5/
../data/negative_sampling_new/dist_mask_True/hi-freq-no-add/1.0/
../data/negative_sampling_new/dist_mask_True/hi-freq/1.0/
../data/negative_sampling_new/dist_mask_False/hi-freq-no-add/1.5/
../data/negative_sampling_new/dist_mask_False/hi-freq-no-add/1.5/
../data/negative_s

In [78]:
data_name = 'hemisphere_hi_dim2'
dist_mask = 'False'
noise_type = 'hi-freq-no-add'
noise_level = 1.0
savefolder = None
plot_x = False
df[(df['data.name'] == data_name) & (df['training.mode'] == 'end2end') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/data/root'] == f'../data/negative_sampling_new/dist_mask_{dist_mask}/{noise_type}/{noise_level}/') & (df['cfg/loss/weights/cycle'] == 1.0)]
# df[(df['data.name'] == data_name) & (df['training.mode'] == 'end2end') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/data/root'] == f'../data/negative_sampling_new/dist_mask_{dist_mask}/{noise_type}/{noise_level}/') & (df['loss.weights.cycle'] == 1.0)]

validation/reconstr_loss  epoch             _wandb  train/loss_epoch  \
46                 58.139244     49  {'runtime': 3106}         15.335145   

    train/dist_loss_epoch  trainer/global_step  train/dist_loss_step  \
46               0.003078               145899              0.003283   

    validation/dist_loss  validation/loss  train/cycle_loss_step  ...  \
46              0.320913         43.61338                0.02929  ...   

    loss.weights.cycle_dist  cfg/decoder/layer_widths  \
46                        0            [64, 128, 256]   

    cfg/encoder/layer_widths  cfg/training/accelerator  \
46            [256, 128, 64]                      cuda   

    cfg/loss/weights/reconstr  cfg/training/weight_decay  \
46                       0.32                     0.0001   

    cfg/loss/weights/cycle_dist  cfg/training/log_every_n_steps  \
46                            0                             100   

   cfg/training/train_valid_split    run_id  
46                            0.8  smmularu  

[1 rows x 80 columns]

In [79]:
len(df)

72

In [108]:
def plot_results(data_name, dist_mask, noise_type, noise_level, plot_x=False, savefolder=None, cycle=1.0):
    run_id = df[(df['data.name'] == data_name) & (df['training.mode'] == 'end2end') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/data/root'] == f'../data/negative_sampling_new/dist_mask_{dist_mask}/{noise_type}/{noise_level}/') & (df['cfg/loss/weights/cycle'] == cycle)].copy()
    assert len(run_id) == 1
    run_id = run_id['run_id'].values[0]
    run = api.run(f"{entity}/{project}/{run_id}")
    folder_path = '../../src/wandb/'
    cfg = OmegaConf.create(run.config)
    folder_list = glob.glob(f"{folder_path}*{run.id}*")
    ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
    ckpt_path = ckpt_files[0]
    cfg.data.root = '../' + cfg.data.root
    model = Autoencoder.load_from_checkpoint(ckpt_path)
    data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
    with torch.no_grad():
        model.eval()
        x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
        z = model.encoder(x)
        xh = model.decoder(z)
        zhh = model.encoder(xh)
    zc = z.cpu().numpy()
    filename = None
    title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
    if savefolder is not None:
        pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
        filename = f"{savefolder}/{title}.html"
    scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
    scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
    if plot_x:
        title = f'[INPUT DATA] {title}'
        if savefolder is not None:
            filename = f"{savefolder}/{title}.html"
        scatter(x, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()


In [105]:
len(df)

72

In [106]:
savefolder = 'embedding_neg_sampl_cycle'

In [109]:
noise = 1.0
plot_results('hemisphere_hi_dim2', 'False', 'hi-freq-no-add', noise, savefolder=savefolder, cycle=1.0)

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning:

Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.



In [110]:
noise = 1.0
plot_results('hemisphere_hi_dim2', 'False', 'hi-freq-no-add', noise, savefolder=savefolder, cycle=10.0)

In [116]:
plot_results('hemisphere_hi_dim2', 'False', 'hi-freq-no-add', noise, savefolder=savefolder, cycle=10.0)

In [111]:
noise = 1.0
plot_results('eb_subset_all', 'False', 'hi-freq-no-add', noise, savefolder=savefolder, cycle=1.0)

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning:

Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.



In [112]:
plot_results('eb_subset_all', 'False', 'hi-freq-no-add', noise, savefolder=savefolder, cycle=10.0)

In [66]:
data_name = 'hemisphere'
dist_mask = 'False'
noise_type = 'hi-freq-no-add'
noise_level = 1.0
savefolder = None
plot_x = False
run_id = df[(df['data.name'] == data_name) & (df['cfg/data/root'] == f'../data/negative_sampling_new/dist_mask_False/hi-freq-no-add/1.0/')]


In [86]:
len(df)

72

In [87]:
run_id['run_id']

7     vndov9te
13    vndov9te
Name: run_id, dtype: object

In [68]:
df[df['run_id'].isin(['wnxhkv9s', 'vn0lcwua', 'ypihn2dy'])]

Empty DataFrame
Columns: [validation/reconstr_loss, epoch, _wandb, train/loss_epoch, train/dist_loss_epoch, trainer/global_step, train/dist_loss_step, validation/dist_loss, validation/loss, train/cycle_loss_step, train/reconstr_loss_step, _step, _timestamp, train/loss_step, train/reconstr_loss_epoch, _runtime, validation/cycle_loss, train/cycle_loss_epoch, data, loss, path, logger, decoder, encoder, training, data.name, data.root, dimensions, preprocessor, cfg/data/name, cfg/data/root, cfg/path/root, training.mode, cfg/path/model, cfg/logger/tags, cfg/training/lr, decoder.dropout, encoder.dropout, cfg/data/filetype, cfg/logger/entity, cfg/training/mode, cfg/training/seed, dimensions.latent, loss.weights.dist, cfg/logger/project, decoder.batch_norm, encoder.batch_norm, loss.weights.cycle, cfg/decoder/dropout, cfg/dimensions/data, cfg/encoder/dropout, loss.dist_mse_decay, training.max_epochs, cfg/logger/use_wandb, cfg/training/monitor, cfg/training/shuffle, decoder.layer_widths, encoder.layer_widths, cfg/dimensions/latent, cfg/loss/weights/dist, cfg/training/patience, loss.weights.reconstr, cfg/decoder/activation, cfg/decoder/batch_norm, cfg/encoder/activation, cfg/encoder/batch_norm, cfg/loss/weights/cycle, cfg/loss/dist_mse_decay, cfg/training/batch_size, cfg/training/max_epochs, loss.weights.cycle_dist, cfg/decoder/layer_widths, cfg/encoder/layer_widths, cfg/training/accelerator, cfg/loss/weights/reconstr, cfg/training/weight_decay, cfg/loss/weights/cycle_dist, cfg/training/log_every_n_steps, cfg/training/train_valid_split, run_id]
Index: []

[0 rows x 80 columns]

In [88]:
len(df['run_id'].unique())

68

In [53]:
len(sweep.runs)

72

In [34]:
noise = 1.0
plot_results('hemisphere', 'False', 'hi-freq-no-add', noise, True, savefolder=savefolder)

AssertionError: 

In [113]:

# run_id = df[(df['data.name'] == data_name) & (df['training.mode'] == 'end2end') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/data/root'] == f'../data/negative_sampling_new/dist_mask_{dist_mask}/{noise_type}/{noise_level}/') & (df['cfg/loss/weights/cycle'] == 1.0)].copy()
# assert len(run_id) == 1
# run_id = run_id['run_id'].values[0]
run_id = 'vpq3avmd'
run = api.run(f"{entity}/{project}/{run_id}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()

if plot_x:
    title = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()

In [114]:

# run_id = df[(df['data.name'] == data_name) & (df['training.mode'] == 'end2end') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/data/root'] == f'../data/negative_sampling_new/dist_mask_{dist_mask}/{noise_type}/{noise_level}/') & (df['cfg/loss/weights/cycle'] == 1.0)].copy()
# assert len(run_id) == 1
# run_id = run_id['run_id'].values[0]
run_id = 'vndov9te'
run = api.run(f"{entity}/{project}/{run_id}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()

if plot_x:
    title = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()